# Your Title Here

**Name(s)**: Kevin Wong, Andrew Yang

**Website Link**: (your website link)

# Introduction
<span style="color:red">Understand the data you have access to. Brainstorm a few questions that interest you about the dataset. Pick one question you plan to investigate further. (As the data science lifecycle tells us, this question may change as you work on your project.)</span>

# Univariate Analysis
<span style="color:red">Look at the distributions of relevant columns separately by using DataFrame operations and drawing at least two relevant plots</span>

# Bivariate Analysis
<span style="color:red">Look at the statistics of pairs of columns to identify possible associations. For instance, you may create scatter plots and plot conditional distributions, or box-plots. You must plot at least two such plots in your notebook. The results of your bivariate analyses will be helpful in identifying interesting hypothesis tests!	</span>

# Interesting Aggregates
<span style="color:red"> Choose columns to group and pivot by and examine aggregate statistics.	</span>

# NMAR Analysis
<span style="color:red"> Recall, to determine whether data are likely NMAR, you must reason about the data generating process; you cannot conclude that data are likely NMAR solely by looking at your data. As such, there’s no code to write here (and hence, nothing to put in your notebook).	</span>

# Missingness Dependency
<span style="color:red"> Pick a column in the dataset with non-trivial missingness to analyze, and perform permutation tests to analyze the dependency of the missingness of this column on other columns. </span>

<span style="color:red">Specifically, find at least one other column that the missingness of your selected column does depend on, and at least one other column that the missingness of your selected column does not depend on. </span>

<span style="color:red"> Tip: Make sure you know the difference between the different types of missingness before approaching that section. Many students in the past have lost credit for mistaking one type of missingness for another. </span>

# Hypothesis Testing
<span style="color:red"> Clearly state a pair of hypotheses and perform a hypothesis test or permutation test that is not related to missingness. Feel free to use the “sample questions” in each of the dataset descriptions or create your own. This should be the question that is stated clearly at the top of your report.	</span>

# Notes

1) GameID has 12 rows - 10 for each of the 5 players on both teams, as well as 2 for the team summary data. To separate it, 'position' column either has the position of the player, or 'team' if it is the summary stat
2) Try to convert boolean columns  
        a) 'datacompleteness' ('complete' - True, 'partial' - False) (NOTE: 'ignore' may be considered True - need to look at further data to compensate)
        b) 'playoffs' - (1 - True, 0 - False)
        c) 'result' - (1 - True, 0 - False)

### datacompleteness - 'Partial' Notes

1) 'Partial' - all data is web scraped from LPL (China), missing a lot because site is missing said data
2) Columns 'doublekill', 'triplekill', 'quadrakill', 'pentakill', 'firstblood', drakeinformation, 'firsttower', 'firstmidtower', 'firsttothreetowers', 'turretplates', 'opp_turretplates', 'damagemitigatedperminute', general gold information

1) Null Hypothesis: For teams that win, the probability of having a winning top lane has no affect on how well the team does

2) Alternative Hypothesis: For teams that win, the probabilityy of having a winning top is significantly higher than when the team loses.

 HYPOTHESES:
1) Null: Having a winning top lane does not affect the probability of the team winning.
2) Alt: Having a winning top lane significantly increases the probability of the team winning.

## Code

In [2]:
import pandas as pd
import numpy as np
import os

import plotly.express as px
pd.options.plotting.backend = 'plotly'

### Cleaning and EDA

In [3]:
df = pd.read_csv("2022_LoL_esports_match_data_from_OraclesElixir.csv")
df

/Users/kevinwong/anaconda3/envs/dsc80/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3505: DtypeWarning: Columns (2,76) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


gameid datacompleteness  \
0       ESPORTSTMNT01_2690210         complete   
1       ESPORTSTMNT01_2690210         complete   
2       ESPORTSTMNT01_2690210         complete   
3       ESPORTSTMNT01_2690210         complete   
4       ESPORTSTMNT01_2690210         complete   
...                       ...              ...   
149395       9687-9687_game_5          partial   
149396       9687-9687_game_5          partial   
149397       9687-9687_game_5          partial   
149398       9687-9687_game_5          partial   
149399       9687-9687_game_5          partial   

                                                url league  year   split  \
0                                               NaN   LCKC  2022  Spring   
1                                               NaN   LCKC  2022  Spring   
2                                               NaN   LCKC  2022  Spring   
3                                               NaN   LCKC  2022  Spring   
4                                               NaN   LCKC  2022  Spring   
...                                             ...    ...   ...     ...   
149395  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  2022     NaN   
149396  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  2022     NaN   
149397  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  2022     NaN   
149398  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  2022     NaN   
149399  https://lpl.qq.com/es/stats.shtml?bmid=9687   DCup  2022     NaN   

        playoffs                 date  game  patch  ...  opp_csat15  \
0              0  2022-01-10 07:44:08     1  12.01  ...       121.0   
1              0  2022-01-10 07:44:08     1  12.01  ...       100.0   
2              0  2022-01-10 07:44:08     1  12.01  ...       119.0   
3              0  2022-01-10 07:44:08     1  12.01  ...       149.0   
4              0  2022-01-10 07:44:08     1  12.01  ...        21.0   
...          ...                  ...   ...    ...  ...         ...   
149395         0  2022-12-27 12:43:43     5  12.23  ...         NaN   
149396         0  2022-12-27 12:43:43     5  12.23  ...         NaN   
149397         0  2022-12-27 12:43:43     5  12.23  ...         NaN   
149398         0  2022-12-27 12:43:43     5  12.23  ...         NaN   
149399         0  2022-12-27 12:43:43     5  12.23  ...         NaN   

       golddiffat15 xpdiffat15 csdiffat15 killsat15 assistsat15 deathsat15  \
0             391.0      345.0       14.0       0.0         1.0        0.0   
1             541.0     -275.0      -11.0       2.0         3.0        2.0   
2            -475.0      153.0        1.0       0.0         3.0        0.0   
3            -793.0    -1343.0      -34.0       2.0         1.0        2.0   
4             443.0     -497.0        7.0       1.0         2.0        2.0   
...             ...        ...        ...       ...         ...        ...   
149395          NaN        NaN        NaN       NaN         NaN        NaN   
149396          NaN        NaN        NaN       NaN         NaN        NaN   
149397          NaN        NaN        NaN       NaN         NaN        NaN   
149398          NaN        NaN        NaN       NaN         NaN        NaN   
149399          NaN        NaN        NaN       NaN         NaN        NaN   

       opp_killsat15 opp_assistsat15 opp_deathsat15  
0                0.0             1.0            0.0  
1                0.0             5.0            1.0  
2                3.0             3.0            2.0  
3                3.0             3.0            0.0  
4                0.0             6.0            2.0  
...              ...             ...            ...  
149395           NaN             NaN            NaN  
149396           NaN             NaN            NaN  
149397           NaN             NaN            NaN  
149398           NaN             NaN            NaN  
149399           NaN             NaN            NaN  

[149400 rows x 123 columns]

In [4]:
# cleaning data: converts columns 'datacompleteness', 'playoffs', 'result'
# we then get the columns that are needed for our hypothesis

cleaned_data = df.assign(
    datacompleteness = df['datacompleteness'].apply(lambda x: True if x == "complete" else False),
    playoffs = df['playoffs'].apply(lambda x: True if x == 1 else False),
    result = df['result'].apply(lambda x: True if x == 1 else False)
    ).loc[
        :, ['gameid', 'datacompleteness', 'playoffs', 'side', 'position', 'champion', 'gamelength', 'result', 'killsat15', 'assistsat15', 'deathsat15', 'goldat15', 'xpat15', 'csat15', 'golddiffat15', 'xpdiffat15', 'csdiffat15']
    ]

In [5]:
cleaned_data.head(12)

gameid  datacompleteness  playoffs  side position  \
0   ESPORTSTMNT01_2690210              True     False  Blue      top   
1   ESPORTSTMNT01_2690210              True     False  Blue      jng   
2   ESPORTSTMNT01_2690210              True     False  Blue      mid   
3   ESPORTSTMNT01_2690210              True     False  Blue      bot   
4   ESPORTSTMNT01_2690210              True     False  Blue      sup   
5   ESPORTSTMNT01_2690210              True     False   Red      top   
6   ESPORTSTMNT01_2690210              True     False   Red      jng   
7   ESPORTSTMNT01_2690210              True     False   Red      mid   
8   ESPORTSTMNT01_2690210              True     False   Red      bot   
9   ESPORTSTMNT01_2690210              True     False   Red      sup   
10  ESPORTSTMNT01_2690210              True     False  Blue     team   
11  ESPORTSTMNT01_2690210              True     False   Red     team   

    champion  gamelength  result  killsat15  assistsat15  deathsat15  \
0   Renekton        1713   False        0.0          1.0         0.0   
1   Xin Zhao        1713   False        2.0          3.0         2.0   
2    LeBlanc        1713   False        0.0          3.0         0.0   
3     Samira        1713   False        2.0          1.0         2.0   
4      Leona        1713   False        1.0          2.0         2.0   
5     Gragas        1713    True        0.0          1.0         0.0   
6      Viego        1713    True        0.0          5.0         1.0   
7     Viktor        1713    True        3.0          3.0         2.0   
8       Jinx        1713    True        3.0          3.0         0.0   
9    Alistar        1713    True        0.0          6.0         2.0   
10       NaN        1713   False        5.0         10.0         6.0   
11       NaN        1713    True        6.0         18.0         5.0   

    goldat15   xpat15  csat15  golddiffat15  xpdiffat15  csdiffat15  
0     5025.0   7560.0   135.0         391.0       345.0        14.0  
1     5366.0   5320.0    89.0         541.0      -275.0       -11.0  
2     5118.0   6942.0   120.0        -475.0       153.0         1.0  
3     5461.0   4591.0   115.0        -793.0     -1343.0       -34.0  
4     3836.0   3588.0    28.0         443.0      -497.0         7.0  
5     4634.0   7215.0   121.0        -391.0      -345.0       -14.0  
6     4825.0   5595.0   100.0        -541.0       275.0        11.0  
7     5593.0   6789.0   119.0         475.0      -153.0        -1.0  
8     6254.0   5934.0   149.0         793.0      1343.0        34.0  
9     3393.0   4085.0    21.0        -443.0       497.0        -7.0  
10   24806.0  28001.0   487.0         107.0     -1617.0       -23.0  
11   24699.0  29618.0   510.0        -107.0      1617.0        23.0

In [6]:
# adding two columns relevant to our investigation of 'winning top'
# teamcs represents the total cs of every position of each side
# teamgold represents the total gold of every position of each side

# generated_df = (cleaned_data
#                 .assign(teamcs = cleaned_data.groupby(['gameid', 'side'])['total cs'].transform(sum))
#                 .assign(teamgold = cleaned_data.groupby(['gameid', 'side'])['totalgold'].transform(lambda col: col.sum()/2))
#                )
# generated_df.head(12)

generated_df = cleaned_data

In [7]:
# filter the dataframe to only get complete data and position that we want to analyze
filtered_df = generated_df[(generated_df['datacompleteness'] == True) & (generated_df['position'] == 'top')]
filtered_df.head(12)

gameid  datacompleteness  playoffs  side position  \
0    ESPORTSTMNT01_2690210              True     False  Blue      top   
5    ESPORTSTMNT01_2690210              True     False   Red      top   
12   ESPORTSTMNT01_2690219              True     False  Blue      top   
17   ESPORTSTMNT01_2690219              True     False   Red      top   
36   ESPORTSTMNT01_2690227              True     False  Blue      top   
41   ESPORTSTMNT01_2690227              True     False   Red      top   
60   ESPORTSTMNT01_2690255              True     False  Blue      top   
65   ESPORTSTMNT01_2690255              True     False   Red      top   
84   ESPORTSTMNT01_2690264              True     False  Blue      top   
89   ESPORTSTMNT01_2690264              True     False   Red      top   
120  ESPORTSTMNT01_2690302              True     False  Blue      top   
125  ESPORTSTMNT01_2690302              True     False   Red      top   

      champion  gamelength  result  killsat15  assistsat15  deathsat15  \
0     Renekton        1713   False        0.0          1.0         0.0   
5       Gragas        1713    True        0.0          1.0         0.0   
12      Gragas        2114   False        0.0          1.0         1.0   
17   Gangplank        2114    True        1.0          0.0         1.0   
36    Renekton        1972    True        2.0          0.0         0.0   
41      Graves        1972   False        0.0          0.0         0.0   
60      Gragas        2488   False        0.0          3.0         0.0   
65        Yone        2488    True        0.0          0.0         1.0   
84      Graves        2020    True        0.0          0.0         0.0   
89        Gwen        2020   False        0.0          0.0         0.0   
120       Gwen        2910    True        0.0          0.0         0.0   
125     Wukong        2910   False        0.0          0.0         0.0   

     goldat15  xpat15  csat15  golddiffat15  xpdiffat15  csdiffat15  
0      5025.0  7560.0   135.0         391.0       345.0        14.0  
5      4634.0  7215.0   121.0        -391.0      -345.0       -14.0  
12     4673.0  7020.0   110.0       -1484.0      -652.0       -30.0  
17     6157.0  7672.0   140.0        1484.0       652.0        30.0  
36     5856.0  7759.0   146.0         904.0        85.0         4.0  
41     4952.0  7674.0   142.0        -904.0       -85.0        -4.0  
60     5251.0  7795.0   147.0         225.0       227.0         5.0  
65     5026.0  7568.0   142.0        -225.0      -227.0        -5.0  
84     6551.0  8412.0   175.0        1728.0       971.0        44.0  
89     4823.0  7441.0   131.0       -1728.0      -971.0       -44.0  
120    4821.0  6336.0   114.0         128.0      -820.0       -17.0  
125    4693.0  7156.0   131.0        -128.0       820.0        17.0

### Univariate Analysis

In [8]:
for col in filtered_df.select_dtypes(include=['number']).columns:
    fig = px.histogram(filtered_df, x=col, title=f'{col} distribution')
    fig.show()

### Bivariate Analysis

In [9]:
fig = px.scatter_matrix(filtered_df.drop(columns=['gameid','datacompleteness','playoffs','gamelength','side','position','champion','golddiffat15','xpdiffat15','csdiffat15']))
fig.show()

In [10]:
#Bivariate using exact value
bivar_result = (filtered_df
                .drop(columns=['datacompleteness','playoffs','gamelength','golddiffat15','xpdiffat15','csdiffat15'])
                .groupby('result')
                .agg('mean')
               )
for col in bivar_result.columns:
    fig = px.bar(bivar_result[[col]])
    fig.show()
bivar_result

killsat15  assistsat15  deathsat15     goldat15       xpat15  \
result                                                                 
False    0.501747     0.580791    0.943715  5071.124280  7164.667674   
True     0.759754     0.855361    0.661030  5401.068304  7391.569391   

            csat15  
result              
False   122.205780  
True    127.033916

In [11]:
#Bivariate using proportions
def prop_calc(col):
    return col / col.max()
bivar_result = pd.melt(
               (filtered_df
                .drop(columns=['datacompleteness','playoffs','gamelength','golddiffat15','xpdiffat15','csdiffat15'])
                .groupby('result')
                .agg('mean')
                .apply(prop_calc)
                .T
                .reset_index()
               ),
                id_vars=['index']
                )
fig = px.bar(bivar_result, x='index', y='value', color='result', barmode='group')
fig.show()
bivar_result

index result     value
0     killsat15  False  0.660407
1   assistsat15  False  0.679001
2    deathsat15  False  1.000000
3      goldat15  False  0.938911
4        xpat15  False  0.969303
5        csat15  False  0.961993
6     killsat15   True  1.000000
7   assistsat15   True  1.000000
8    deathsat15   True  0.700455
9      goldat15   True  1.000000
10       xpat15   True  1.000000
11       csat15   True  1.000000

### Assessment of Missingness

In [12]:
# To assess missingness, we want to analyze what is actually missing
missing_data = pd.DataFrame(df.isnull().sum()).T
missing_data

gameid  datacompleteness     url  league  year  split  playoffs  date  \
0       0                 0  126984       0     0  39972         0     0   

   game  patch  ...  opp_csat15  golddiffat15  xpdiffat15  csdiffat15  \
0     0    108  ...       21828         21828       21828       21828   

   killsat15  assistsat15  deathsat15  opp_killsat15  opp_assistsat15  \
0      21828        21828       21828          21828            21828   

   opp_deathsat15  
0           21828  

[1 rows x 123 columns]

In [37]:
# We've seen that a lot of out data is missing, especially near the end of the data; specifically, 
# things like 'opp_csat15', 'golddiffat15', and more are missing. In this case, we want to test if there's
# a specific reason why this data may be missing; 
missing_important_data = df[df['opp_csat15'].isnull()]

# Here, we want to get rid of unnecessary columns that won't be needed for both a permutation test and
# one's that have mostly unique columns, because otherwise we won't be able to compare distributions easily
missing_important_data = missing_important_data.loc[:, ['league', 'split', 'playoffs', 'patch', 'position']]
missing_important_data

league   split  playoffs  patch position
24        LPL  Spring         0  12.01      top
25        LPL  Spring         0  12.01      jng
26        LPL  Spring         0  12.01      mid
27        LPL  Spring         0  12.01      bot
28        LPL  Spring         0  12.01      sup
...       ...     ...       ...    ...      ...
149395   DCup     NaN         0  12.23      mid
149396   DCup     NaN         0  12.23      bot
149397   DCup     NaN         0  12.23      sup
149398   DCup     NaN         0  12.23     team
149399   DCup     NaN         0  12.23     team

[21828 rows x 5 columns]

In [38]:
# we are going to find what to test what type of data is missing when analyzing the different 
league_dependence = missing_important_data.groupby('league')['playoffs'].count()
split_dependence = missing_important_data.groupby('split')['playoffs'].count()
playoff_depedence = missing_important_data.groupby('playoffs')['playoffs'].count()
patch_dependence = missing_important_data.groupby('patch')['playoffs'].count()
position_dependence = missing_important_data.groupby('position')['playoffs'].count()

# while looking through these, we can see some stark observations
# for 'league_dependence', although we have 49 leagues, only 4 show up here
# for 'split_dependence', we had a relatively even amount of missing for each split
# for 'playoff_depedence', most were non-playoff games, but that may be an indication of the amount of playoff games vs normal games
# for 'patch_dependence', it was all over the place
for data in [league_dependence, split_dependence, playoff_depedence, patch_dependence, position_dependence]:
    fig = px.bar(data/data.sum())
    fig.show()


In [39]:
# Now, let's do a permutation test on the overall dataframe to see if the missing values have the same distribution as this
# If they don't then it is likely that this column and the other columns are MAR 
test_df = (df
           .assign(league = np.random.permutation(df['league']))
           .assign(split = np.random.permutation(df['split']))
           .assign(playoffs = np.random.permutation(df['playoffs']))
           .assign(patch = np.random.permutation(df['patch']))
           .assign(position = np.random.permutation(df['position']))
           )
           
test_df = test_df[test_df['opp_csat15'].isnull()].loc[:, ['league', 'split', 'playoffs', 'patch', 'position']]
test_df

league    split  playoffs  patch position
24        LMF  Split 1         0  12.01      mid
25        LCK      NaN         0  12.14     team
26        LDL   Summer         0  12.18      jng
27         GL  Champ 1         0  12.20      mid
28        LDL   Spring         0  12.02      jng
...       ...      ...       ...    ...      ...
149395   LFL2   Summer         0  12.18      sup
149396    LFL  Split 2         0  12.02      mid
149397    LPL   Pro-Am         1  12.12      bot
149398    LFL   Spring         0  12.11      mid
149399  LPLOL      NaN         0  12.13     team

[21828 rows x 5 columns]

In [40]:
league_dependence = test_df.groupby('league')['playoffs'].count()
split_dependence = test_df.groupby('split')['playoffs'].count()
playoff_depedence = test_df.groupby('playoffs')['playoffs'].count()
patch_dependence = test_df.groupby('patch')['playoffs'].count()
position_dependence = test_df.groupby('position')['playoffs'].count()

for data in [league_dependence, split_dependence, playoff_depedence, patch_dependence, position_dependence]:
    fig = px.bar(data/data.sum())
    fig.show()

In [17]:
test_df = df.assign(league = np.random.permutation)
stats = test_df[test_df['opp_csat15'].isnull()].groupby('league')['playoffs'].count()

In [18]:
# just through observing the graphs, the most stark difference comes from the regions, where it seems like LPL
# and LDL carry the most missing values (both are from China). In order to test this, let's compare the highest 
# in our filtered data set (LDL, 0.517867)

# In this case, these are our hypotheses (testing at the 0.01 significance level)
# Null Hypothesis: Data that is missing comes from the same 'league' distribution as all other data
# Alternative Hypothesis: Data that is missing is significantly more likely to be one 'league' than others

differences = []
for _ in range(1000):
    test_df = df.assign(league = np.random.permutation(df['league']))
    stats = test_df[test_df['opp_csat15'].isnull()].groupby('league')['playoffs'].count()
    differences.append(stats[stats.index == 'LDL'].iloc[0]/stats.sum())
    
p_value = np.mean(np.array(differences) >= 0.517867)

In [19]:
# Since our p-value is 0, this means that the missing of the 'opp_csat15' is reliant on the 'league' column,
# particularly when testing with the LDL and LPL teams (Chinese). These possibly suggest that there is an issue
# with getting Chinese Data on these columns, or that Chinese teams don't record this data

p_value

0.0

In [41]:
# Now for testing something else that might have a different missingness, we want to see if there's anything that 
# could reasonably be different based on randomness. If we look at the number of times missingness was determined
# based on the playoffs, the highest total percentage was 0.8801539. Let's test this with a null and alternative hypotheses

# Null Hypothesis: The missingness of NA values in the 'opp_csat15' column comes from the same distribution regardless of the position player's have played
# Alternative Hypothesis: The missingness of NA values in 'opp_csat15' column is not dependent on a position played

position_differences = []
for _ in range(1000):
    test_df = df.assign(position = np.random.permutation(df['position']))
    stats = test_df[test_df['opp_csat15'].isnull()].groupby('position')['gameid'].count()
    position_differences.append(stats.iloc[0]/stats.sum())

position_pval = np.mean(np.array(position_differences) >= (1/6))

In [42]:
# Since our p-value is over 0.01 (our significance level), we can accept our null hypothesis and state that
# the missingness of column 'opp_csat15' is not dependent on the position being played by players at the time

position_pval

0.489

### Hypothesis Testing

In [ ]:
# TODO
# We need to operationalize what winning means
# First we can add columns for KDA((Kills + Assists) / Deaths) as well as killparticipation

# def kda_calc(df):
#     return (df['kills'] + df['assists']) / max(df['deaths'], 1)
# def killpart_calc(df):
#     if df['teamkills'] == 0:
#         return 0
#     return (df['kills'] + df['assists']) / df['teamkills']

def winning_top(df):
    if df['xpdiffat15'] > 0:
        return True
    elif df['xpdiffat15'] < 0:
        return False
    return np.NaN

df = (filtered_df
#       .assign(kda = filtered_df.apply(kda_calc, axis=1))
#       .assign(killpart = filtered_df.apply(killpart_calc, axis=1))
      .assign(winlane = filtered_df.apply(winning_top, axis=1))
     )
df

gameid  datacompleteness  playoffs  side position  \
0       ESPORTSTMNT01_2690210              True     False  Blue      top   
5       ESPORTSTMNT01_2690210              True     False   Red      top   
12      ESPORTSTMNT01_2690219              True     False  Blue      top   
17      ESPORTSTMNT01_2690219              True     False   Red      top   
36      ESPORTSTMNT01_2690227              True     False  Blue      top   
...                       ...               ...       ...   ...      ...   
149105  ESPORTSTMNT01_3268686              True     False   Red      top   
149112  ESPORTSTMNT01_3269631              True     False  Blue      top   
149117  ESPORTSTMNT01_3269631              True     False   Red      top   
149124  ESPORTSTMNT01_3268705              True     False  Blue      top   
149129  ESPORTSTMNT01_3268705              True     False   Red      top   

         champion  gamelength  result  killsat15  assistsat15  deathsat15  \
0        Renekton        1713   False        0.0          1.0         0.0   
5          Gragas        1713    True        0.0          1.0         0.0   
12         Gragas        2114   False        0.0          1.0         1.0   
17      Gangplank        2114    True        1.0          0.0         1.0   
36       Renekton        1972    True        2.0          0.0         0.0   
...           ...         ...     ...        ...          ...         ...   
149105    K'Sante        2325    True        0.0          1.0         2.0   
149112      Fiora        2076    True        2.0          1.0         1.0   
149117    K'Sante        2076   False        0.0          1.0         3.0   
149124  Gangplank        1680    True        2.0          1.0         2.0   
149129    K'Sante        1680   False        2.0          0.0         1.0   

        goldat15  xpat15  csat15  golddiffat15  xpdiffat15  csdiffat15 winlane  
0         5025.0  7560.0   135.0         391.0       345.0        14.0    True  
5         4634.0  7215.0   121.0        -391.0      -345.0       -14.0   False  
12        4673.0  7020.0   110.0       -1484.0      -652.0       -30.0   False  
17        6157.0  7672.0   140.0        1484.0       652.0        30.0    True  
36        5856.0  7759.0   146.0         904.0        85.0         4.0    True  
...          ...     ...     ...           ...         ...         ...     ...  
149105    4782.0  7650.0   122.0        -801.0       829.0        11.0    True  
149112    7262.0  8025.0   137.0        2728.0      1467.0        32.0    True  
149117    4534.0  6558.0   105.0       -2728.0     -1467.0       -32.0   False  
149124    6485.0  7618.0   123.0        1537.0       645.0        15.0    True  
149129    4948.0  6973.0   108.0       -1537.0      -645.0       -15.0   False  

[21174 rows x 18 columns]

In [ ]:
df['winlane'].unique

<bound method Series.unique of 0          True
5         False
12        False
17         True
36         True
          ...  
149105     True
149112     True
149117    False
149124     True
149129    False
Name: winlane, Length: 21174, dtype: object>